In [153]:
#note: temp readings are 20s apart

import pandas as pd
import os
import matplotlib.pyplot as plt
import random
import tensorflow as tf
from keras.models import Sequential
from keras.layers import Dense, BatchNormalization, Normalization
import numpy as np

In [ ]:
os.chdir('data')

In [120]:
dfs = {}# dictionary of dataframes

for folder in os.listdir():
    if os.path.isdir(folder):
        os.chdir(folder)
        for file in os.listdir():
            try:
                df = pd.read_excel(file, sheet_name="DATA", usecols='C,D', skiprows = 1)
                df.columns = ['temp', 'label']
                df.loc[df.shape[0]] = [None, None]# to ensure that there are breaks between each recorded shower
                dfs[file] = df
            except:
                print(file)
        os.chdir('..')
        
data = pd.concat(list(dfs.values()), ignore_index = True)# concatenating all our data into one big dataframe

~$Reduced Burt-W2a SN 20461395 2019-04-10 16_30_57 -0400.xlsx
~$Copy of Dascomb 20461369 2019-12-02 18_07_58 -0500.xlsx


# Shortest end to peak distance

In [44]:
shortest = 100 #arbitrary upper bound


for key in dfs.keys():
    i = 0
    last_end = 0
    df = dfs[key]
    while i < len(df['label']):
        if isinstance(df.loc[i, 'label'], str):
            if df.loc[i, 'label'].startswith('End'):
                last_end = i
            if df.loc[i, 'label'].startswith('Peak'):
                shortest = min(shortest, i - last_end)
                shortest_index = i
                file = key
        i += 1
    
print(f'shortest end to peak distance: {shortest}')
print(f'file: {file}')
print(f'index: {shortest_index}')

shortest end to peak distance: 3
file: Reduced Kahn S2c 20569773 2019-04-26 09_54_34 -0400.xlsx
index: 1226


This distance is too small, so we will instead base our window size on the shortest distance from the desired feature to an upper/lower bound of our data

# Shortest start to 'out of range' distance

In [45]:
shortest = 100

for key in dfs.keys():
    i = 0
    last_out = -1
    last_start = 0
    df = dfs[key]
    while i < len(df['label']):
        if isinstance(df.loc[i, 'label'], str):
            if df.loc[i, 'label'].startswith('Start'):
                last_start = i
                if i - last_out < shortest:
                    shortest = i - last_out
                    shortest_index = last_out
                    file = key
        if np.isnan(df.loc[i, 'temp']):
            if i - last_start < shortest:
                shortest = i - last_start
                shortest_index = last_start
                file = key
            last_out = i
        i += 1
    
print(f"shortest start to 'out of range' distance: {shortest}")
print(f'file: {file}')
print(f'index: {shortest_index}')

shortest start to 'out of range' distance: 11
file: Reduced Kahn S2e 20569774 2019-04-26 09_56_01 -0400.xlsx
index: -1


Shortest start to 'out of range' distance is 11, so we make our window size $2 \cdot (11 - 1) -1 = 19$, to account for the case where the 'out of range' is 11 indices away on both sides.

# Shortest end to 'out of range' distance

In [48]:
shortest = 100

for key in dfs.keys():
    i = 0
    last_out = -1
    last_end = 0
    df = dfs[key]
    while i < len(df['label']):
        if isinstance(df.loc[i, 'label'], str):
            if df.loc[i, 'label'].startswith('End'):
                last_end = i
                if i - last_out < shortest:
                    shortest = i - last_out
                    shortest_index = last_out
                    file = key
        if np.isnan(df.loc[i, 'temp']):
            if i - last_end < shortest:
                shortest = i - last_end
                shortest_index = last_end
                file = key
            last_out = i
        i += 1
    
print(f"shortest end to 'out of range' distance: {shortest}")
print(f'file: {file}')
print(f'index: {shortest_index}')

shortest end to 'out of range' distance: 14
file: Reduced Kahn S2e 20569774 2019-04-26 09_56_01 -0400.xlsx
index: 416


Shortest end to 'out of range' distance is 14, so we make our window size $2 \cdot (14 - 1) -1 = 25$, as before.

In [132]:
# start window size: 19
# end window size: 25
start_pts = []#list where the first item is 1 for start and 0 for not start
end_pts = []#same list but for ends

for i, row in data.iterrows():
    if not pd.isnull(row['label']):
        if row['label'].startswith('Start'):
            start_pts.append([1] + data.iloc[i-9:i+10]['temp'].tolist())
        if row['label'].startswith('End'):
            end_pts.append([1] + data.iloc[i-12:i+13]['temp'].tolist())
initial_length = len(start_pts)
if initial_length != len(end_pts):
    print("inconsistent labels!")

#taking a random sample of indices (without replacement) of size k
random_start_indices = random.sample(range(len(data) - 19), k =  len(data) - 19)
random_end_indices = random.sample(range(len(data) - 25), k = len(data) - 25)

for i in random_start_indices:
    if not (any(pd.isnull(data.iloc[i:i+19//2]['temp'])) or
            (not pd.isnull(data.iloc[i+19//2]['label']) and data.iloc[i+19//2]['label'].startswith('Start'))):
        start_pts.append([0] + data.iloc[i:i+19]['temp'].tolist())
        if len(start_pts) == initial_length * 2:
            break

for i in random_end_indices:
    if not (any(pd.isnull(data.iloc[i:i+25//2]['temp'])) or
            (not pd.isnull(data.iloc[i+25//2]['label']) and data.iloc[i+25//2]['label'].startswith('End'))):
        end_pts.append([0] + data.iloc[i:i+25]['temp'].tolist())
        if len(end_pts) == initial_length * 2:
            break

In [133]:
start_data = np.asarray(start_pts)#tensors holding the label, followed by a list of 10 temperatures
np.random.shuffle(start_data)

end_data = np.asarray(end_pts)
np.random.shuffle(end_data)

In [134]:
data_length = start_data.shape[0]

start_train = start_data[:int(data_length * .7)]
start_val = start_data[int(data_length * .7):int(data_length * .85)]
start_test = start_data[int(data_length * .85):]

end_train = end_data[:int(data_length * .7)]
end_val = end_data[int(data_length * .7):int(data_length * .85)]
end_test = end_data[int(data_length * .85):]

In [140]:
start_model = Sequential(
    [
        BatchNormalization(),
        Dense(16, activation = 'relu', input_shape=(19,)),
        Dense(16, activation = 'relu'),
        Dense(1, activation = 'sigmoid')
    ]
)

start_model.compile(loss='mse', metrics=['mae'])
start_model.fit(start_train[:,1:], start_train[:,0], epochs=2000)
start_val_predicted = start_model.predict(start_val[:,1:])

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2500 - mae: 0.4958
Epoch 2/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2457 - mae: 0.4910
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2456 - mae: 0.4916
Epoch 4/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2419 - mae: 0.4885
Epoch 5/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2384 - mae: 0.4847
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2377 - mae: 0.4842
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2362 - mae: 0.4826
Epoch 8/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2358 - mae: 0.4822
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2351 - mae: 0.4794
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2365 - mae: 0.4820
Epoch 11/2000
5/5 [==============================] - 0s 1ms/step - lo

5/5 [==============================] - 0s 1ms/step - loss: 0.1551 - mae: 0.3247
Epoch 175/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1486 - mae: 0.3226
Epoch 176/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1547 - mae: 0.3283
Epoch 177/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1543 - mae: 0.3258
Epoch 178/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1413 - mae: 0.3117
Epoch 179/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1505 - mae: 0.3239
Epoch 180/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1418 - mae: 0.3146
Epoch 181/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1617 - mae: 0.3309
Epoch 182/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1623 - mae: 0.3291
Epoch 183/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1870 - mae: 0.3515
Epoch 184/2000
5/5 [==============================] - 0s 2ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.1566 - mae: 0.3153
Epoch 347/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1442 - mae: 0.2896
Epoch 348/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1450 - mae: 0.3011
Epoch 349/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1426 - mae: 0.2905
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1294 - mae: 0.2800
Epoch 351/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1398 - mae: 0.2923
Epoch 352/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1464 - mae: 0.2978
Epoch 353/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1333 - mae: 0.2817
Epoch 354/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1370 - mae: 0.2933
Epoch 355/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1248 - mae: 0.2808
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.1436 - mae: 0.2873
Epoch 519/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1484 - mae: 0.2943
Epoch 520/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1285 - mae: 0.2691
Epoch 521/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1399 - mae: 0.2877
Epoch 522/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1427 - mae: 0.2792
Epoch 523/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1370 - mae: 0.2788
Epoch 524/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1473 - mae: 0.2888
Epoch 525/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1327 - mae: 0.2755
Epoch 526/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1462 - mae: 0.2820
Epoch 527/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1533 - mae: 0.2927
Epoch 528/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.1506 - mae: 0.2942
Epoch 691/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1313 - mae: 0.2730
Epoch 692/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1209 - mae: 0.2602
Epoch 693/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1759 - mae: 0.3214
Epoch 694/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1370 - mae: 0.2840
Epoch 695/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1395 - mae: 0.2841
Epoch 696/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1179 - mae: 0.2609
Epoch 697/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1349 - mae: 0.2831
Epoch 698/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1338 - mae: 0.2784
Epoch 699/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1221 - mae: 0.2644
Epoch 700/2000
5/5 [==============================] - 0s 2ms/step

...

5/5 [==============================] - 0s 1ms/step - loss: 0.1376 - mae: 0.2692
Epoch 1205/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1229 - mae: 0.2602
Epoch 1206/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1132 - mae: 0.2429
Epoch 1207/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1174 - mae: 0.2500
Epoch 1208/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1661 - mae: 0.3001
Epoch 1209/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1181 - mae: 0.2515
Epoch 1210/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1766 - mae: 0.3058
Epoch 1211/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1629 - mae: 0.2937
Epoch 1212/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1362 - mae: 0.2656
Epoch 1213/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1578 - mae: 0.2918
Epoch 1214/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1157 - mae: 0.2379
Epoch 1375/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1211 - mae: 0.2465
Epoch 1376/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1368 - mae: 0.2611
Epoch 1377/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1219 - mae: 0.2482
Epoch 1378/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1092 - mae: 0.2381
Epoch 1379/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1339 - mae: 0.2667
Epoch 1380/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1357 - mae: 0.2709
Epoch 1381/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1291 - mae: 0.2661
Epoch 1382/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1317 - mae: 0.2676
Epoch 1383/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1208 - mae: 0.2585
Epoch 1384/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1097 - mae: 0.2332
Epoch 1545/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1343 - mae: 0.2635
Epoch 1546/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1331 - mae: 0.2610
Epoch 1547/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1375 - mae: 0.2698
Epoch 1548/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1254 - mae: 0.2534
Epoch 1549/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1208 - mae: 0.2544
Epoch 1550/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1317 - mae: 0.2577
Epoch 1551/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1149 - mae: 0.2461
Epoch 1552/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1264 - mae: 0.2622
Epoch 1553/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1083 - mae: 0.2361
Epoch 1554/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.1223 - mae: 0.2502
Epoch 1715/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1201 - mae: 0.2451
Epoch 1716/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1196 - mae: 0.2486
Epoch 1717/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1243 - mae: 0.2499
Epoch 1718/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1094 - mae: 0.2379
Epoch 1719/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1513 - mae: 0.2819
Epoch 1720/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1274 - mae: 0.2521
Epoch 1721/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1240 - mae: 0.2463
Epoch 1722/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1561 - mae: 0.2856
Epoch 1723/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1464 - mae: 0.2780
Epoch 1724/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.1218 - mae: 0.2511
Epoch 1885/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1503 - mae: 0.2827
Epoch 1886/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1300 - mae: 0.2558
Epoch 1887/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1234 - mae: 0.2532
Epoch 1888/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1185 - mae: 0.2429
Epoch 1889/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1173 - mae: 0.2470
Epoch 1890/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1356 - mae: 0.2624
Epoch 1891/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1084 - mae: 0.2414
Epoch 1892/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1271 - mae: 0.2680
Epoch 1893/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1269 - mae: 0.2570
Epoch 1894/2000
5/5 [==============================] - 0

In [142]:
np.mean(np.absolute(start_val_predicted[:,0] - start_val[:,0]))

0.21153241495291392

In [149]:
end_model = Sequential(
    [
        BatchNormalization(),
        Dense(16, activation = 'relu', input_shape=(25,)),
        Dense(16, activation = 'relu'),
        Dense(1, activation = 'sigmoid')
    ]
)

end_model.compile(loss='mse', metrics=['mae'])
end_model.fit(end_train[:,1:], end_train[:,0], epochs=2000)
end_val_predicted = end_model.predict(end_val[:,1:])

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1910 - mae: 0.4147
Epoch 2/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1707 - mae: 0.3838
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1618 - mae: 0.3633
Epoch 4/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1569 - mae: 0.3528
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1504 - mae: 0.3408
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1459 - mae: 0.3330
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1415 - mae: 0.3248
Epoch 8/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1370 - mae: 0.3172
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1375 - mae: 0.3160
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1267 - mae: 0.2983
Epoch 11/2000
5/5 [==============================] - 0s 2ms/step - lo

5/5 [==============================] - 0s 1ms/step - loss: 0.0767 - mae: 0.1550
Epoch 175/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0742 - mae: 0.1462
Epoch 176/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0840 - mae: 0.1657
Epoch 177/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0698 - mae: 0.1467
Epoch 178/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0682 - mae: 0.1462
Epoch 179/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0682 - mae: 0.1468
Epoch 180/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0824 - mae: 0.1700
Epoch 181/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1023 - mae: 0.1705
Epoch 182/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0853 - mae: 0.1683
Epoch 183/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0806 - mae: 0.1620
Epoch 184/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1598
Epoch 347/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0694 - mae: 0.1498
Epoch 348/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0774 - mae: 0.1434
Epoch 349/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0637 - mae: 0.1311
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0702 - mae: 0.1356
Epoch 351/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0954 - mae: 0.1846
Epoch 352/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0672 - mae: 0.1290
Epoch 353/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0752 - mae: 0.1458
Epoch 354/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0836 - mae: 0.1529
Epoch 355/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0796 - mae: 0.1482
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0712 - mae: 0.1525
Epoch 519/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0786 - mae: 0.1606
Epoch 520/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0825 - mae: 0.1636
Epoch 521/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0730 - mae: 0.1435
Epoch 522/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0953 - mae: 0.1753
Epoch 523/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0752 - mae: 0.1332
Epoch 524/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0759 - mae: 0.1411
Epoch 525/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0834 - mae: 0.1673
Epoch 526/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0657 - mae: 0.1347
Epoch 527/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0915 - mae: 0.1633
Epoch 528/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 2ms/step - loss: 0.0709 - mae: 0.1523
Epoch 691/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0772 - mae: 0.1558
Epoch 692/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0749 - mae: 0.1521
Epoch 693/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0836 - mae: 0.1745
Epoch 694/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0615 - mae: 0.1315
Epoch 695/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0717 - mae: 0.1497
Epoch 696/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0841 - mae: 0.1757
Epoch 697/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0743 - mae: 0.1537
Epoch 698/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0647 - mae: 0.1418
Epoch 699/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0695 - mae: 0.1471
Epoch 700/2000
5/5 [==============================] - 0s 1ms/step

...

5/5 [==============================] - 0s 1ms/step - loss: 0.0606 - mae: 0.1413
Epoch 1205/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0714 - mae: 0.1522
Epoch 1206/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0836 - mae: 0.1547
Epoch 1207/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0646 - mae: 0.1368
Epoch 1208/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0933 - mae: 0.1661
Epoch 1209/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0666 - mae: 0.1305
Epoch 1210/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0848 - mae: 0.1616
Epoch 1211/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0645 - mae: 0.1359
Epoch 1212/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0707 - mae: 0.1450
Epoch 1213/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0682 - mae: 0.1392
Epoch 1214/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.0649 - mae: 0.1354
Epoch 1375/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0750 - mae: 0.1510
Epoch 1376/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0827 - mae: 0.1615
Epoch 1377/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0676 - mae: 0.1306
Epoch 1378/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0986 - mae: 0.1663
Epoch 1379/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0677 - mae: 0.1369
Epoch 1380/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0555 - mae: 0.1286
Epoch 1381/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0742 - mae: 0.1469
Epoch 1382/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0676 - mae: 0.1474
Epoch 1383/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0579 - mae: 0.1223
Epoch 1384/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.0697 - mae: 0.1422
Epoch 1545/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0609 - mae: 0.1400
Epoch 1546/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0864 - mae: 0.1743
Epoch 1547/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0637 - mae: 0.1308
Epoch 1548/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0600 - mae: 0.1340
Epoch 1549/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0622 - mae: 0.1361
Epoch 1550/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0674 - mae: 0.1382
Epoch 1551/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0811 - mae: 0.1477
Epoch 1552/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0758 - mae: 0.1320
Epoch 1553/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0620 - mae: 0.1302
Epoch 1554/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0693 - mae: 0.1466
Epoch 1715/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0707 - mae: 0.1338
Epoch 1716/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0695 - mae: 0.1429
Epoch 1717/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0674 - mae: 0.1407
Epoch 1718/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0719 - mae: 0.1515
Epoch 1719/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0591 - mae: 0.1298
Epoch 1720/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0703 - mae: 0.1579
Epoch 1721/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0847 - mae: 0.1631
Epoch 1722/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0604 - mae: 0.1321
Epoch 1723/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0653 - mae: 0.1312
Epoch 1724/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.1019 - mae: 0.1800
Epoch 1885/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0654 - mae: 0.1457
Epoch 1886/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0682 - mae: 0.1372
Epoch 1887/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0860 - mae: 0.1636
Epoch 1888/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0626 - mae: 0.1271
Epoch 1889/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0838 - mae: 0.1736
Epoch 1890/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0673 - mae: 0.1328
Epoch 1891/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0655 - mae: 0.1262
Epoch 1892/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0628 - mae: 0.1254
Epoch 1893/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0662 - mae: 0.1270
Epoch 1894/2000
5/5 [==============================] - 0

In [150]:
np.mean(np.absolute(end_val_predicted[:,0] - end_val[:,0]))

0.10680945118268331

# one hidden layer:

In [145]:
start_model = Sequential(
    [
        BatchNormalization(),
        Dense(16, activation = 'relu', input_shape=(19,)),
        Dense(1, activation = 'sigmoid')
    ]
)

start_model.compile(loss='mse', metrics=['mae'])
start_model.fit(start_train[:,1:], start_train[:,0], epochs=2000)
start_val_predicted = start_model.predict(start_val[:,1:])

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2601 - mae: 0.4729
Epoch 2/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2492 - mae: 0.4727
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2390 - mae: 0.4702
Epoch 4/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2377 - mae: 0.4736
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2304 - mae: 0.4734
Epoch 6/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2264 - mae: 0.4673
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2263 - mae: 0.4680
Epoch 8/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2233 - mae: 0.4645
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2238 - mae: 0.4656
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2208 - mae: 0.4609
Epoch 11/2000
5/5 [==============================] - 0s 2ms/step - lo

5/5 [==============================] - 0s 1ms/step - loss: 0.1736 - mae: 0.3694
Epoch 175/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1561 - mae: 0.3520
Epoch 176/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1584 - mae: 0.3479
Epoch 177/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1759 - mae: 0.3671
Epoch 178/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1772 - mae: 0.3727
Epoch 179/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1655 - mae: 0.3611
Epoch 180/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1847 - mae: 0.3762
Epoch 181/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1669 - mae: 0.3663
Epoch 182/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1594 - mae: 0.3512
Epoch 183/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1614 - mae: 0.3548
Epoch 184/2000
5/5 [==============================] - 0s 2ms/step

5/5 [==============================] - 0s 2ms/step - loss: 0.1423 - mae: 0.3187
Epoch 347/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1568 - mae: 0.3324
Epoch 348/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1433 - mae: 0.3145
Epoch 349/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1475 - mae: 0.3241
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1489 - mae: 0.3250
Epoch 351/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1645 - mae: 0.3339
Epoch 352/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1429 - mae: 0.3169
Epoch 353/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1676 - mae: 0.3447
Epoch 354/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1465 - mae: 0.3158
Epoch 355/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1560 - mae: 0.3328
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 2ms/step - loss: 0.1436 - mae: 0.3070
Epoch 519/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1620 - mae: 0.3275
Epoch 520/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1439 - mae: 0.3077
Epoch 521/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1179 - mae: 0.2813
Epoch 522/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1549 - mae: 0.3259
Epoch 523/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1432 - mae: 0.3067
Epoch 524/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1420 - mae: 0.3020
Epoch 525/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1382 - mae: 0.3075
Epoch 526/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1595 - mae: 0.3160
Epoch 527/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1693 - mae: 0.3240
Epoch 528/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 2ms/step - loss: 0.1739 - mae: 0.3296
Epoch 691/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1354 - mae: 0.2841
Epoch 692/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1831 - mae: 0.3370
Epoch 693/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1473 - mae: 0.2949
Epoch 694/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1398 - mae: 0.2959
Epoch 695/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1514 - mae: 0.3143
Epoch 696/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1409 - mae: 0.3088
Epoch 697/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1621 - mae: 0.3131
Epoch 698/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1421 - mae: 0.2994
Epoch 699/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1593 - mae: 0.3110
Epoch 700/2000
5/5 [==============================] - 0s 1ms/step

...

5/5 [==============================] - 0s 1ms/step - loss: 0.1493 - mae: 0.2962
Epoch 1205/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1252 - mae: 0.2689
Epoch 1206/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1627 - mae: 0.3094
Epoch 1207/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1320 - mae: 0.2796
Epoch 1208/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1565 - mae: 0.3085
Epoch 1209/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1305 - mae: 0.2826
Epoch 1210/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1294 - mae: 0.2789
Epoch 1211/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1213 - mae: 0.2722
Epoch 1212/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1195 - mae: 0.2637
Epoch 1213/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1323 - mae: 0.2760
Epoch 1214/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.1228 - mae: 0.2624
Epoch 1375/2000
5/5 [==============================] - 0s 4ms/step - loss: 0.1326 - mae: 0.2788
Epoch 1376/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1356 - mae: 0.2796
Epoch 1377/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1516 - mae: 0.2866
Epoch 1378/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1393 - mae: 0.2797
Epoch 1379/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1173 - mae: 0.2583
Epoch 1380/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1336 - mae: 0.2796
Epoch 1381/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1438 - mae: 0.2853
Epoch 1382/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1333 - mae: 0.2724
Epoch 1383/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1368 - mae: 0.2760
Epoch 1384/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1300 - mae: 0.2745
Epoch 1545/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1313 - mae: 0.2737
Epoch 1546/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1708 - mae: 0.3127
Epoch 1547/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1583 - mae: 0.3025
Epoch 1548/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1376 - mae: 0.2845
Epoch 1549/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1303 - mae: 0.2718
Epoch 1550/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1205 - mae: 0.2611
Epoch 1551/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1431 - mae: 0.2896
Epoch 1552/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1245 - mae: 0.2599
Epoch 1553/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1385 - mae: 0.2797
Epoch 1554/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1503 - mae: 0.2927
Epoch 1715/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1339 - mae: 0.2798
Epoch 1716/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1157 - mae: 0.2582
Epoch 1717/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1440 - mae: 0.2938
Epoch 1718/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1105 - mae: 0.2503
Epoch 1719/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1335 - mae: 0.2840
Epoch 1720/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1318 - mae: 0.2798
Epoch 1721/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1404 - mae: 0.2796
Epoch 1722/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1216 - mae: 0.2583
Epoch 1723/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1486 - mae: 0.2953
Epoch 1724/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.1142 - mae: 0.2538
Epoch 1885/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1581 - mae: 0.2918
Epoch 1886/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1180 - mae: 0.2510
Epoch 1887/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1494 - mae: 0.2809
Epoch 1888/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1579 - mae: 0.2943
Epoch 1889/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1560 - mae: 0.2946
Epoch 1890/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1901 - mae: 0.3315
Epoch 1891/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1165 - mae: 0.2461
Epoch 1892/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1196 - mae: 0.2566
Epoch 1893/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1313 - mae: 0.2741
Epoch 1894/2000
5/5 [==============================] - 0

In [146]:
np.mean(np.absolute(start_val_predicted[:,0] - start_val[:,0]))

0.20048483510812123

In [160]:
end_model = Sequential(
    [
        BatchNormalization(),
        Dense(16, activation = 'relu', input_shape=(25,)),
        Dense(1, activation = 'sigmoid')
    ]
)

end_model.compile(loss='mse', metrics=['mae'])
end_model.fit(end_train[:,1:], end_train[:,0], epochs=2000)
end_val_predicted = end_model.predict(end_val[:,1:])

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2227 - mae: 0.4330
Epoch 2/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1924 - mae: 0.4019
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1788 - mae: 0.3814
Epoch 4/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1735 - mae: 0.3720
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1719 - mae: 0.3667
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1641 - mae: 0.3534
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1560 - mae: 0.3429
Epoch 8/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1513 - mae: 0.3347
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1561 - mae: 0.3348
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1528 - mae: 0.3301
Epoch 11/2000
5/5 [==============================] - 0s 2ms/step - lo

5/5 [==============================] - 0s 2ms/step - loss: 0.0786 - mae: 0.1585
Epoch 175/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1038 - mae: 0.1926
Epoch 176/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0739 - mae: 0.1603
Epoch 177/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0723 - mae: 0.1661
Epoch 178/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0824 - mae: 0.1720
Epoch 179/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0799 - mae: 0.1670
Epoch 180/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0818 - mae: 0.1664
Epoch 181/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0777 - mae: 0.1588
Epoch 182/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0798 - mae: 0.1653
Epoch 183/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0721 - mae: 0.1573
Epoch 184/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0956 - mae: 0.1804
Epoch 347/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0757 - mae: 0.1545
Epoch 348/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0757 - mae: 0.1573
Epoch 349/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0756 - mae: 0.1623
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0780 - mae: 0.1602
Epoch 351/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0787 - mae: 0.1510
Epoch 352/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0845 - mae: 0.1724
Epoch 353/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0786 - mae: 0.1590
Epoch 354/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1050 - mae: 0.1793
Epoch 355/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0988 - mae: 0.1862
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0793 - mae: 0.1519
Epoch 519/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0731 - mae: 0.1514
Epoch 520/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0748 - mae: 0.1507
Epoch 521/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0760 - mae: 0.1521
Epoch 522/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0662 - mae: 0.1405
Epoch 523/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0788 - mae: 0.1485
Epoch 524/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0684 - mae: 0.1375
Epoch 525/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0792 - mae: 0.1633
Epoch 526/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0758 - mae: 0.1531
Epoch 527/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1041 - mae: 0.1860
Epoch 528/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 2ms/step - loss: 0.0851 - mae: 0.1633
Epoch 691/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0701 - mae: 0.1449
Epoch 692/2000
5/5 [==============================] - 0s 3ms/step - loss: 0.0752 - mae: 0.1542
Epoch 693/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0712 - mae: 0.1368
Epoch 694/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0789 - mae: 0.1430
Epoch 695/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0791 - mae: 0.1507
Epoch 696/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0693 - mae: 0.1395
Epoch 697/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0794 - mae: 0.1580
Epoch 698/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1302 - mae: 0.2192
Epoch 699/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0796 - mae: 0.1550
Epoch 700/2000
5/5 [==============================] - 0s 1ms/step

...

5/5 [==============================] - 0s 1ms/step - loss: 0.0756 - mae: 0.1583
Epoch 1205/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0760 - mae: 0.1473
Epoch 1206/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0803 - mae: 0.1506
Epoch 1207/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0808 - mae: 0.1599
Epoch 1208/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0689 - mae: 0.1406
Epoch 1209/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0764 - mae: 0.1482
Epoch 1210/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0665 - mae: 0.1423
Epoch 1211/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0754 - mae: 0.1449
Epoch 1212/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0758 - mae: 0.1516
Epoch 1213/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0703 - mae: 0.1417
Epoch 1214/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0747 - mae: 0.1491
Epoch 1375/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0744 - mae: 0.1599
Epoch 1376/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0696 - mae: 0.1417
Epoch 1377/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0692 - mae: 0.1387
Epoch 1378/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0811 - mae: 0.1609
Epoch 1379/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0903 - mae: 0.1641
Epoch 1380/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0678 - mae: 0.1295
Epoch 1381/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0726 - mae: 0.1369
Epoch 1382/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0883 - mae: 0.1599
Epoch 1383/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0793 - mae: 0.1509
Epoch 1384/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0713 - mae: 0.1394
Epoch 1545/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0757 - mae: 0.1472
Epoch 1546/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0679 - mae: 0.1423
Epoch 1547/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0671 - mae: 0.1367
Epoch 1548/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0999 - mae: 0.1928
Epoch 1549/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0641 - mae: 0.1358
Epoch 1550/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0689 - mae: 0.1423
Epoch 1551/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0806 - mae: 0.1539
Epoch 1552/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0799 - mae: 0.1544
Epoch 1553/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0829 - mae: 0.1585
Epoch 1554/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0714 - mae: 0.1478
Epoch 1715/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0669 - mae: 0.1426
Epoch 1716/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1120 - mae: 0.2081
Epoch 1717/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0638 - mae: 0.1408
Epoch 1718/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0740 - mae: 0.1524
Epoch 1719/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0691 - mae: 0.1532
Epoch 1720/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0714 - mae: 0.1390
Epoch 1721/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0725 - mae: 0.1462
Epoch 1722/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0678 - mae: 0.1307
Epoch 1723/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0679 - mae: 0.1319
Epoch 1724/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0773 - mae: 0.1459
Epoch 1885/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0787 - mae: 0.1566
Epoch 1886/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0649 - mae: 0.1323
Epoch 1887/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0698 - mae: 0.1369
Epoch 1888/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0835 - mae: 0.1588
Epoch 1889/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0818 - mae: 0.1656
Epoch 1890/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0686 - mae: 0.1352
Epoch 1891/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0750 - mae: 0.1412
Epoch 1892/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1053 - mae: 0.1730
Epoch 1893/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0745 - mae: 0.1429
Epoch 1894/2000
5/5 [==============================] - 0

In [161]:
np.mean(np.absolute(end_val_predicted[:,0] - end_val[:,0]))

0.11648958722750345

# manual normalization:

In [162]:
start_model = Sequential(
    [
        Dense(16, activation = 'relu', input_shape=(19,)),
        Dense(1, activation = 'sigmoid')
    ]
)

start_model.compile(loss='mse', metrics=['mae'])

min_start_temp = np.min(start_train[:,1:])
max_start_temp = np.max(start_train[:,1:])

def start_normalize(array):
    return (array-min_start_temp)/max_start_temp

start_model.fit(normalize(start_train[:,1:]), start_train[:,0], epochs=2000)
start_val_predicted = start_model.predict(normalize(start_val[:,1:]))

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2492 - mae: 0.4988
Epoch 2/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2487 - mae: 0.4984
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2481 - mae: 0.4975
Epoch 4/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2481 - mae: 0.4974
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2476 - mae: 0.4960
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2478 - mae: 0.4965
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2481 - mae: 0.4964
Epoch 8/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2474 - mae: 0.4958
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2474 - mae: 0.4955
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2474 - mae: 0.4960
Epoch 11/2000
5/5 [==============================] - 0s 2ms/step - lo

5/5 [==============================] - 0s 1ms/step - loss: 0.2375 - mae: 0.4848
Epoch 175/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2380 - mae: 0.4848
Epoch 176/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2378 - mae: 0.4848
Epoch 177/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2374 - mae: 0.4852
Epoch 178/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2372 - mae: 0.4843
Epoch 179/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2374 - mae: 0.4838
Epoch 180/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2372 - mae: 0.4840
Epoch 181/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2375 - mae: 0.4851
Epoch 182/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2371 - mae: 0.4842
Epoch 183/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2374 - mae: 0.4850
Epoch 184/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.2266 - mae: 0.4704
Epoch 347/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2270 - mae: 0.4701
Epoch 348/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2266 - mae: 0.4704
Epoch 349/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2263 - mae: 0.4706
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2266 - mae: 0.4705
Epoch 351/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2263 - mae: 0.4692
Epoch 352/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2265 - mae: 0.4701
Epoch 353/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2262 - mae: 0.4699
Epoch 354/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2263 - mae: 0.4699
Epoch 355/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2261 - mae: 0.4697
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.2149 - mae: 0.4536
Epoch 519/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2155 - mae: 0.4547
Epoch 520/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2153 - mae: 0.4547
Epoch 521/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2148 - mae: 0.4551
Epoch 522/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2152 - mae: 0.4550
Epoch 523/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2150 - mae: 0.4551
Epoch 524/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2147 - mae: 0.4539
Epoch 525/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2146 - mae: 0.4546
Epoch 526/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2153 - mae: 0.4556
Epoch 527/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2144 - mae: 0.4540
Epoch 528/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.2051 - mae: 0.4397
Epoch 691/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2055 - mae: 0.4401
Epoch 692/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2047 - mae: 0.4394
Epoch 693/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2065 - mae: 0.4408
Epoch 694/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2052 - mae: 0.4391
Epoch 695/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2047 - mae: 0.4395
Epoch 696/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2047 - mae: 0.4393
Epoch 697/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2042 - mae: 0.4386
Epoch 698/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2045 - mae: 0.4386
Epoch 699/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2051 - mae: 0.4389
Epoch 700/2000
5/5 [==============================] - 0s 1ms/step

...

5/5 [==============================] - 0s 2ms/step - loss: 0.1855 - mae: 0.4037
Epoch 1205/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1862 - mae: 0.4046
Epoch 1206/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1855 - mae: 0.4037
Epoch 1207/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1856 - mae: 0.4037
Epoch 1208/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1854 - mae: 0.4029
Epoch 1209/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1852 - mae: 0.4033
Epoch 1210/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1850 - mae: 0.4032
Epoch 1211/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1853 - mae: 0.4033
Epoch 1212/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1851 - mae: 0.4030
Epoch 1213/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1864 - mae: 0.4038
Epoch 1214/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1809 - mae: 0.3952
Epoch 1375/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1814 - mae: 0.3958
Epoch 1376/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1829 - mae: 0.3966
Epoch 1377/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1806 - mae: 0.3951
Epoch 1378/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1812 - mae: 0.3947
Epoch 1379/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1802 - mae: 0.3947
Epoch 1380/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1813 - mae: 0.3957
Epoch 1381/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1821 - mae: 0.3967
Epoch 1382/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1808 - mae: 0.3947
Epoch 1383/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1814 - mae: 0.3951
Epoch 1384/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1774 - mae: 0.3887
Epoch 1545/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1775 - mae: 0.3886
Epoch 1546/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1769 - mae: 0.3880
Epoch 1547/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1775 - mae: 0.3881
Epoch 1548/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1778 - mae: 0.3888
Epoch 1549/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1770 - mae: 0.3880
Epoch 1550/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1786 - mae: 0.3893
Epoch 1551/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1770 - mae: 0.3880
Epoch 1552/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1778 - mae: 0.3891
Epoch 1553/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1765 - mae: 0.3874
Epoch 1554/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1731 - mae: 0.3813
Epoch 1715/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1729 - mae: 0.3807
Epoch 1716/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1734 - mae: 0.3812
Epoch 1717/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1731 - mae: 0.3817
Epoch 1718/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1735 - mae: 0.3807
Epoch 1719/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1737 - mae: 0.3817
Epoch 1720/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1743 - mae: 0.3818
Epoch 1721/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1739 - mae: 0.3825
Epoch 1722/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1739 - mae: 0.3822
Epoch 1723/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1725 - mae: 0.3808
Epoch 1724/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.1704 - mae: 0.3744
Epoch 1885/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1706 - mae: 0.3742
Epoch 1886/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1694 - mae: 0.3743
Epoch 1887/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1712 - mae: 0.3756
Epoch 1888/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1695 - mae: 0.3731
Epoch 1889/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1693 - mae: 0.3735
Epoch 1890/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1688 - mae: 0.3740
Epoch 1891/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1689 - mae: 0.3733
Epoch 1892/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1713 - mae: 0.3750
Epoch 1893/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1687 - mae: 0.3738
Epoch 1894/2000
5/5 [==============================] - 0

In [163]:
np.mean(np.absolute(start_val_predicted[:,0] - start_val[:,0]))

0.36282771130402885

In [164]:
end_model = Sequential(
    [
        BatchNormalization(),
        Dense(16, activation = 'relu', input_shape=(25,)),
        Dense(1, activation = 'sigmoid')
    ]
)

min_end_temp = np.min(start_train[:,1:])
max_end_temp = np.max(start_train[:,1:])

def end_normalize(array):
    return (array-min_end_temp)/max_end_temp

end_model.compile(loss='mse', metrics=['mae'])
end_model.fit(normalize(end_train[:,1:]), end_train[:,0], epochs=2000)
end_val_predicted = end_model.predict(normalize(end_val[:,1:]))

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2921 - mae: 0.5282
Epoch 2/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2419 - mae: 0.4852
Epoch 3/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2140 - mae: 0.4555
Epoch 4/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1962 - mae: 0.4311
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1875 - mae: 0.4149
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1907 - mae: 0.4134
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1786 - mae: 0.3938
Epoch 8/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1741 - mae: 0.3841
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1698 - mae: 0.3757
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1642 - mae: 0.3675
Epoch 11/2000
5/5 [==============================] - 0s 2ms/step - lo

5/5 [==============================] - 0s 1ms/step - loss: 0.0911 - mae: 0.1915
Epoch 175/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0924 - mae: 0.1886
Epoch 176/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0846 - mae: 0.1819
Epoch 177/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0872 - mae: 0.1795
Epoch 178/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0848 - mae: 0.1748
Epoch 179/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0886 - mae: 0.1776
Epoch 180/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0953 - mae: 0.1866
Epoch 181/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0750 - mae: 0.1691
Epoch 182/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0801 - mae: 0.1729
Epoch 183/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0884 - mae: 0.1937
Epoch 184/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0749 - mae: 0.1552
Epoch 347/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0837 - mae: 0.1573
Epoch 348/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0759 - mae: 0.1486
Epoch 349/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0744 - mae: 0.1483
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0726 - mae: 0.1404
Epoch 351/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0853 - mae: 0.1639
Epoch 352/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0722 - mae: 0.1540
Epoch 353/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0727 - mae: 0.1483
Epoch 354/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0848 - mae: 0.1599
Epoch 355/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0841 - mae: 0.1633
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0820 - mae: 0.1609
Epoch 519/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0956 - mae: 0.1658
Epoch 520/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0818 - mae: 0.1611
Epoch 521/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0892 - mae: 0.1675
Epoch 522/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0696 - mae: 0.1458
Epoch 523/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0736 - mae: 0.1477
Epoch 524/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0729 - mae: 0.1432
Epoch 525/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0717 - mae: 0.1465
Epoch 526/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0785 - mae: 0.1512
Epoch 527/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0866 - mae: 0.1666
Epoch 528/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.0672 - mae: 0.1367
Epoch 691/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0699 - mae: 0.1373
Epoch 692/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0685 - mae: 0.1390
Epoch 693/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.1048 - mae: 0.1928
Epoch 694/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0671 - mae: 0.1370
Epoch 695/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0763 - mae: 0.1472
Epoch 696/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0758 - mae: 0.1423
Epoch 697/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0729 - mae: 0.1433
Epoch 698/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0716 - mae: 0.1388
Epoch 699/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0890 - mae: 0.1661
Epoch 700/2000
5/5 [==============================] - 0s 1ms/step

...

5/5 [==============================] - 0s 1ms/step - loss: 0.0797 - mae: 0.1482
Epoch 1205/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0810 - mae: 0.1537
Epoch 1206/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0704 - mae: 0.1329
Epoch 1207/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0805 - mae: 0.1607
Epoch 1208/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0669 - mae: 0.1491
Epoch 1209/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0725 - mae: 0.1481
Epoch 1210/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0697 - mae: 0.1432
Epoch 1211/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0693 - mae: 0.1348
Epoch 1212/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0861 - mae: 0.1641
Epoch 1213/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0760 - mae: 0.1445
Epoch 1214/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.0687 - mae: 0.1303
Epoch 1375/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0702 - mae: 0.1447
Epoch 1376/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0679 - mae: 0.1369
Epoch 1377/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0702 - mae: 0.1381
Epoch 1378/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0732 - mae: 0.1419
Epoch 1379/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0662 - mae: 0.1302
Epoch 1380/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0690 - mae: 0.1380
Epoch 1381/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0970 - mae: 0.1841
Epoch 1382/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0737 - mae: 0.1373
Epoch 1383/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0799 - mae: 0.1477
Epoch 1384/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0800 - mae: 0.1477
Epoch 1545/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0701 - mae: 0.1303
Epoch 1546/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0759 - mae: 0.1447
Epoch 1547/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0688 - mae: 0.1333
Epoch 1548/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0761 - mae: 0.1398
Epoch 1549/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0673 - mae: 0.1359
Epoch 1550/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.1061 - mae: 0.1746
Epoch 1551/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0831 - mae: 0.1537
Epoch 1552/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0818 - mae: 0.1420
Epoch 1553/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0760 - mae: 0.1422
Epoch 1554/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 2ms/step - loss: 0.0725 - mae: 0.1433
Epoch 1715/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0748 - mae: 0.1395
Epoch 1716/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.0842 - mae: 0.1509
Epoch 1717/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0657 - mae: 0.1372
Epoch 1718/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0774 - mae: 0.1477
Epoch 1719/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0922 - mae: 0.1712
Epoch 1720/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0752 - mae: 0.1424
Epoch 1721/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0806 - mae: 0.1424
Epoch 1722/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0655 - mae: 0.1252
Epoch 1723/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0718 - mae: 0.1334
Epoch 1724/2000
5/5 [==============================] - 0

5/5 [==============================] - 0s 1ms/step - loss: 0.0718 - mae: 0.1498
Epoch 1885/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0738 - mae: 0.1564
Epoch 1886/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0845 - mae: 0.1592
Epoch 1887/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0789 - mae: 0.1596
Epoch 1888/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0694 - mae: 0.1344
Epoch 1889/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0705 - mae: 0.1381
Epoch 1890/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0702 - mae: 0.1323
Epoch 1891/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0725 - mae: 0.1426
Epoch 1892/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0964 - mae: 0.1754
Epoch 1893/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.0717 - mae: 0.1372
Epoch 1894/2000
5/5 [==============================] - 0

In [165]:
np.mean(np.absolute(end_val_predicted[:,0] - end_val[:,0]))

0.10165001451969147

# varying number of neurons:

In [171]:
start_maes = []
end_maes = []

for n in range(0,18):
    start_model = Sequential(
        [
            BatchNormalization(),
            Dense(2**n, activation = 'relu', input_shape=(19,)),
            Dense(1, activation = 'sigmoid')
        ]
    )

    start_model.compile(loss='mse', metrics=['mae'])
    start_model.fit(start_train[:,1:], start_train[:,0], epochs=2000)
    start_val_predicted = start_model.predict(start_val[:,1:])
    
    end_model = Sequential(
        [
            BatchNormalization(),
            Dense(2**n, activation = 'relu', input_shape=(25,)),
            Dense(1, activation = 'sigmoid')
        ]
    )

    end_model.compile(loss='mse', metrics=['mae'])
    end_model.fit(end_train[:,1:], end_train[:,0], epochs=2000)
    end_val_predicted = end_model.predict(end_val[:,1:])
    
    start_maes.append(np.mean(np.absolute(start_val_predicted[:,0] - start_val[:,0])))
    end_maes.append(np.mean(np.absolute(end_val_predicted[:,0] - end_val[:,0])))
    

Epoch 1/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.3343 - mae: 0.5276
Epoch 2/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.3287 - mae: 0.5266
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.3333 - mae: 0.5358
Epoch 4/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.3219 - mae: 0.5309
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.3177 - mae: 0.5296
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.3153 - mae: 0.5290
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.3042 - mae: 0.5230
Epoch 8/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2965 - mae: 0.5191
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2989 - mae: 0.5255
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2972 - mae: 0.5262
Epoch 11/2000
5/5 [==============================] - 0s 2ms/step - lo

5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4990
Epoch 89/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4990
Epoch 90/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4990
Epoch 91/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4990
Epoch 92/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4990
Epoch 93/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4990
Epoch 94/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4990
Epoch 95/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4990
Epoch 96/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4990
Epoch 97/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4989
Epoch 98/2000
5/5 [==============================] - 0s 2ms/step - loss: 0

5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 175/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4988
Epoch 176/2000
5/5 [==============================] - 0s 3ms/step - loss: 0.2494 - mae: 0.4988
Epoch 177/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4988
Epoch 178/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4988
Epoch 179/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4988
Epoch 180/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4988
Epoch 181/2000
5/5 [==============================] - 0s 2ms/step - loss: 0.2494 - mae: 0.4988
Epoch 182/2000
5/5 [==============================] - 0s 7ms/step - loss: 0.2494 - mae: 0.4988
Epoch 183/2000
5/5 [==============================] - 0s 4ms/step - loss: 0.2494 - mae: 0.4988
Epoch 184/2000
5/5 [==============================] - 0s 4ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 261/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 262/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 263/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 264/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 265/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 266/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 267/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 268/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 269/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 270/2000
5/5 [==============================] - 0s 1ms/step

5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 347/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 348/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 349/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 350/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 351/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 352/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 353/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 354/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 355/2000
5/5 [==============================] - 0s 1ms/step - loss: 0.2494 - mae: 0.4988
Epoch 356/2000
5/5 [==============================] - 0s 1ms/step

...

5/5 [==============================] - 0s 37ms/step - loss: 0.0686 - mae: 0.0969
Epoch 1599/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.1171 - mae: 0.1385
Epoch 1600/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0742 - mae: 0.0955
Epoch 1601/2000
5/5 [==============================] - 0s 41ms/step - loss: 0.0776 - mae: 0.0983
Epoch 1602/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0892 - mae: 0.1087
Epoch 1603/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.0968 - mae: 0.1324
Epoch 1604/2000
5/5 [==============================] - 0s 42ms/step - loss: 0.0781 - mae: 0.1032
Epoch 1605/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.1422 - mae: 0.1708
Epoch 1606/2000
5/5 [==============================] - 0s 39ms/step - loss: 0.0854 - mae: 0.1128
Epoch 1607/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0767 - mae: 0.0951
Epoch 1608/2000
5/5 [=========================

5/5 [==============================] - 0s 36ms/step - loss: 0.0696 - mae: 0.0877
Epoch 1683/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0729 - mae: 0.0905
Epoch 1684/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0893 - mae: 0.1110
Epoch 1685/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0699 - mae: 0.0943
Epoch 1686/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.0642 - mae: 0.0815
Epoch 1687/2000
5/5 [==============================] - 0s 39ms/step - loss: 0.0752 - mae: 0.0981
Epoch 1688/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.0879 - mae: 0.1189
Epoch 1689/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0571 - mae: 0.0789
Epoch 1690/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0659 - mae: 0.0876
Epoch 1691/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.0718 - mae: 0.1068
Epoch 1692/2000
5/5 [=========================

5/5 [==============================] - 0s 38ms/step - loss: 0.0925 - mae: 0.1215
Epoch 1767/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.1179 - mae: 0.1417
Epoch 1768/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0685 - mae: 0.0945
Epoch 1769/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0745 - mae: 0.1006
Epoch 1770/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0954 - mae: 0.1183
Epoch 1771/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0990 - mae: 0.1219
Epoch 1772/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0797 - mae: 0.1003
Epoch 1773/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0752 - mae: 0.0945
Epoch 1774/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0786 - mae: 0.1065
Epoch 1775/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0974 - mae: 0.1282
Epoch 1776/2000
5/5 [=========================

5/5 [==============================] - 0s 40ms/step - loss: 0.0616 - mae: 0.0824
Epoch 1851/2000
5/5 [==============================] - 0s 43ms/step - loss: 0.0679 - mae: 0.0908
Epoch 1852/2000
5/5 [==============================] - 0s 43ms/step - loss: 0.1073 - mae: 0.1392
Epoch 1853/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.0889 - mae: 0.1069
Epoch 1854/2000
5/5 [==============================] - 0s 38ms/step - loss: 0.1021 - mae: 0.1255
Epoch 1855/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.1270 - mae: 0.1512
Epoch 1856/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0822 - mae: 0.1038
Epoch 1857/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0854 - mae: 0.1044
Epoch 1858/2000
5/5 [==============================] - 0s 42ms/step - loss: 0.0857 - mae: 0.1037
Epoch 1859/2000
5/5 [==============================] - 0s 45ms/step - loss: 0.1168 - mae: 0.1474
Epoch 1860/2000
5/5 [=========================

5/5 [==============================] - 0s 35ms/step - loss: 0.0664 - mae: 0.0854
Epoch 1935/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0569 - mae: 0.0772
Epoch 1936/2000
5/5 [==============================] - 0s 35ms/step - loss: 0.0846 - mae: 0.1076
Epoch 1937/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0847 - mae: 0.0969
Epoch 1938/2000
5/5 [==============================] - 0s 35ms/step - loss: 0.0727 - mae: 0.0892
Epoch 1939/2000
5/5 [==============================] - 0s 35ms/step - loss: 0.0681 - mae: 0.0884
Epoch 1940/2000
5/5 [==============================] - 0s 37ms/step - loss: 0.0576 - mae: 0.0811
Epoch 1941/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0790 - mae: 0.0990
Epoch 1942/2000
5/5 [==============================] - 0s 35ms/step - loss: 0.0673 - mae: 0.0832
Epoch 1943/2000
5/5 [==============================] - 0s 36ms/step - loss: 0.0770 - mae: 0.1016
Epoch 1944/2000
5/5 [=========================

In [172]:
start_maes

[0.5050673007965087,
 0.5047443866729736,
 0.24326194822788239,
 0.2134235143661499,
 0.21709273358186085,
 0.19371256232261658,
 0.19377480844656628,
 0.20069107512633005,
 0.20500228305657706,
 0.20968445936838787,
 0.2008090039094289,
 0.16390961408615112,
 0.18432040214538575,
 0.1572707881530126,
 0.18688287536303202,
 0.1779700885216395,
 0.162230317791303,
 0.22268733084201814]

In [174]:
start_maes.index(min(start_maes))

13

In [173]:
end_maes

[0.12114745179812113,
 0.12142481803894042,
 0.09879046082496643,
 0.10198091665903727,
 0.10549473762512207,
 0.1074775497118632,
 0.097852690021197,
 0.10163691639900208,
 0.08595996995766958,
 0.08654134074846903,
 0.08301180998484294,
 0.08475075364112854,
 0.08220278620719909,
 0.07860314274633873,
 0.06760215129080469,
 0.0668455660343182,
 0.07504058423148005,
 0.07207128405655201]

In [175]:
end_maes.index(min(end_maes))

15